In [1]:
#import modules

import pandas as pd
import numpy as np

from bokeh.models import *
from bokeh.plotting import *
from bokeh.io import *
from bokeh.tile_providers import *
from bokeh.palettes import *
from bokeh.transform import *
from bokeh.layouts import *

In [2]:
#import and clean the data

conflict_df=pd.read_csv('https://raw.githubusercontent.com/ConnerBrew/Iraq-Conflict-Data/master/conflict_data_irq.csv')
conflict_df=conflict_df.loc[conflict_df['year'] == '2019']
conflict_df['latitude']=conflict_df['latitude'].astype('float')
conflict_df['longitude']=conflict_df['longitude'].astype('float')
conflict_df['fatalities']=conflict_df['fatalities'].astype('int64')
conflict_df=conflict_df.reset_index()
conflict_df=conflict_df.drop('index',axis=1)

In [3]:
#Bokeh maps are in mercator. Convert lat lon fields to mercator units for plotting

def wgs84_to_web_mercator(df, lon, lat):
    """Converts decimal longitude/latitude to Web Mercator format"""
    k = 6378137
    df["x"] = df[lon] * (k * np.pi/180.0)
    df["y"] = np.log(np.tan((90 + df[lat]) * np.pi/360.0)) * k
    return df

df=wgs84_to_web_mercator(conflict_df,'longitude','latitude')

In [4]:
#Establishing a zoom scale for the map. The scale variable will also determine proportions for hexbins and bubble maps so that everything looks visually appealing. 

scale=2000
x=df['x']
y=df['y']

#The range for the map extents is derived from the lat/lon fields. This way the map is automatically centered on the plot elements.

x_min=int(x.mean() - (scale * 350))
x_max=int(x.mean() + (scale * 350))
y_min=int(y.mean() - (scale * 350))
y_max=int(y.mean() + (scale * 350))

#Defining the map tiles to use. I use OSM, but you can also use ESRI images or google street maps.

tile_provider=get_provider(OSM)

#Establish the bokeh plot object and add the map tile as an underlay. Hide x and y axis.

plot=figure(
    title='2019 Iraq Conflict Events',
    match_aspect=True,
    tools='wheel_zoom,pan,reset,save',
    x_range=(x_min, x_max),
    y_range=(y_min, y_max),
    x_axis_type='mercator',
    y_axis_type='mercator'
    )

plot.grid.visible=True

map=plot.add_tile(tile_provider)
map.level='underlay'

plot.xaxis.visible = False
plot.yaxis.visible=False

#If in Jupyter, use the output_notebook() method to display the plot in-line. If not, you can use output_file() or another method to save your map. 
output_notebook()

Loading BokehJS ...

In [5]:
#function takes scale (defined above), the initialized plot object, and the converted dataframe with mercator coordinates to create a hexbin map

def hex_map(plot,df, scale,leg_label='Hexbin Heatmap'):
  r,bins=plot.hexbin(x,y,size=scale*10,hover_color='pink',hover_alpha=0.8,legend_label=leg_label)
  hex_hover = HoverTool(tooltips=[('count','@c')],mode='mouse',point_policy='follow_mouse',renderers=[r])
  hex_hover.renderers.append(r)
  plot.tools.append(hex_hover)
  
  plot.legend.location = "top_right"
  plot.legend.click_policy="hide"

In [6]:
#function takes a column to determine radius and the dataframe with converted mercator coordinates to create a bubble map. 
def bubble_map(plot,df,radius_col,lon,lat,scale,color='orange',leg_label='Bubble Map'):
  radius=[]
  for i in df[radius_col]:
    radius.append(i*scale)
  
  df['radius']=radius
    
  source=ColumnDataSource(df)
  c=plot.circle(x='x',y='y',color=color,source=source,size=1,fill_alpha=0.4,radius='radius',legend_label=leg_label,hover_color='red')

  tip_label='@'+radius_col
  lat_label='@'+lat
  lon_label='@'+lon

  circle_hover = HoverTool(tooltips=[(radius_col,tip_label),('Lat:',lat_label),('Lon:',lon_label)],mode='mouse',point_policy='follow_mouse',renderers=[c])
  circle_hover.renderers.append(c)
  plot.tools.append(circle_hover)

#The legend.click_policy method allows us to toggle layer on/off by clicking the corresponding field in the legend. We'll explore this more later!
  plot.legend.location = "top_right"
  plot.legend.click_policy="hide"

In [7]:
#Create the hexbin map
hex_map(plot=plot,
        df=conflict_df, 
        scale=scale,
        leg_label='Iraq Conflict Events by Number of Events')

#Create the bubble map. In this case, circle radius is defined by the amount of fatalities. Any column can be chosen to define the radius.
bubble_map(plot=plot,
           df=conflict_df,
           radius_col='fatalities', 
           leg_label='Iraq Conflict Events by Fatality',
           lon='longitude',
           lat='latitude',
           scale=scale)

#let's see our handiwork!
show(plot)

In [8]:
#Creating a second map that will display events categorically by type

p=figure(
    title='2019 Iraq Conflict Events by Category',
    match_aspect=True,
    tools='wheel_zoom,pan,reset,save',
    x_range=(x_min, x_max),
    y_range=(y_min, y_max),
    x_axis_type='mercator',
    y_axis_type='mercator')

p.grid.visible=True

m=p.add_tile(tile_provider)
m.level='underlay'

p.xaxis.visible = False
p.yaxis.visible=False

In [9]:
'''Removing duplicate event types using the dictionary method. 
Though there are other ways to remove duplicates from a list, this is my preferred method for simplicity.'''

events=list(conflict_df['event_type'].dropna(how=None))
event_dict=dict.fromkeys(events,0)
events=list(event_dict)

#Initializing empty lists to create temporary dataframes for each category

Protests=[]
Strategic_developments=[]
Riots=[]
Battles=[]
Explosions_remote_violence=[]
Violence_against_civilians=[]
list_list=[Protests,Strategic_developments,Riots,Battles,Explosions_remote_violence,Violence_against_civilians]


In [10]:
for i in range(len(df['event_type'])):
  if df.loc[i,'event_type']=='Protests':
    Protests.append([df.loc[i,'event_type'],
                     df.loc[i,'x'],df.loc[i,'y'],
                     df.loc[i,'actor1'],
                     df.loc[i,'notes'],
                     df.loc[i,'latitude'],
                     df.loc[i,'longitude']])

In [11]:
#using the list of lists, create temporary dataframes for each event category and plot them to our second map.

for i in range(len(list_list)):
  temp_df=pd.DataFrame(list_list[i],columns=['event_type','x','y','actor1','notes','latitude','longitude'])
  source=ColumnDataSource(temp_df)

  circle=p.circle(x='x',y='y',source=source,color=Spectral6[i],line_color=Spectral6[i],legend_label=events[i],hover_color='white',radius=15000,fill_alpha=0.4)

  event_hover = HoverTool(tooltips=[('Actor','@actor1'),
                                    ('Category','@event_type'),
                                    ('Description','@notes'),
                                    ('(Lat,Lon)','(@latitude,@longitude)')],
                          mode='mouse',
                          point_policy='follow_mouse',
                          renderers=[circle])
  
  event_hover.renderers.append(circle)
  p.tools.append(event_hover)

In [12]:
p.legend.location = "top_right"
p.legend.click_policy="hide"
show(row(plot,p))

El enlace

[https://ichi.pro/es/sube-de-nivel-tus-visualizaciones-crea-mapas-interactivos-con-python-y-bokeh-134742211629565]